# Conversational Search

In this notebook you will implement the following steps:

- **Answer selection + evaluation**: Implement a *search-based* conversation framework evaluation framework to evaluate conversation topics made up of conversation turns.
- **Answer ranking**: Implement a *re-ranking method* to sort the initial search results. Evaluate the re-ranked results.
- **Conversation context**: Implement a conversational context modeling method to keep track of the conversation state. 

Submission dates:
- **20 October**: retrieval + evaluation
- **20 November**: pass
age re-ranking
- **20 December**: conversation state tracking

## Test bed and conversation topics
The TREC CAST corpus (http://www.treccast.ai/) for Conversational Search is indexed in this cluster and available to be searched behind an ElasticSearch API.

The queries and the relevance judgments are available through class `ConvSearchEvaluation`:

# Google Colab Setup

The following steps are already implemented in the cell bellow. You need to download the starting project folder, upload it, adjust the paths, and finally run the notebook.


1.   Download the shared project folder as a zip;
2.   Unzip and re-upload to a folder of your own GDrive;
3.   Mount your GDrive on the Colab working environment;

Note: You will be asked to complete a Google Authorization procedure by following a link and pasting a code on the notebook.

4.   Copy the contents from the folder you uploaded to the Colab working dir;
5.   Add sys path locations to run aux Python scripts;
6.   Install dependencies.

After going though all these steps you should be able to run all the cells in the notebook.

In [1]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [2]:
# Colab Setup
# Mount your Google Drive
from google.colab import drive
drive.mount('/content/drive')

# After downloading the shared starting point folder as a Zip
# Unzip it and re-upload it to a location on your GDrive

# This command copies the contents from the folder you uploaded to GDrive, to the colab working dir
!cp -r /content/drive/My\ Drive/faculdade/fct-miei/04_ano4/semestre1/ri/ProjectoRI2020 /content

# Add working dir to the sys path, so that we can find the aux python files when running the Notebook
import sys
if not '/content/ProjectoRI2020' in sys.path:
  sys.path += ['/content/ProjectoRI2020']

# Finally install required dependencies to run the notebook
!pip install elasticsearch
!pip install bert-serving-client

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [3]:
import TRECCASTeval as trec
import numpy as np

from sklearn.metrics.pairwise import cosine_similarity

import ElasticSearchSimpleAPI as es
import numpy as np

import pprint as pprint

test_bed = trec.ConvSearchEvaluation()

print()
print("========================================== Training conversations =====")
topics = {}
for topic in test_bed.train_topics:
    conv_id = topic['number']

    if conv_id not in (1, 2, 4, 7, 15, 17,18,22,23,24,25,27,30):
        continue

    print()
    print(conv_id, "  ", topic['title'])

    for turn in topic['turn']:
        turn_id = turn['number']
        utterance = turn['raw_utterance']
        topic_turn_id = '%d_%d'% (conv_id, turn_id)
        
        print(topic_turn_id, utterance)
        topics[topic_turn_id] = utterance

print()
print("========================================== Test conversations =====")
for topic in test_bed.test_topics:
    conv_id = topic['number']

    if conv_id not in (31, 32, 33, 34, 37, 40, 49, 50, 54, 56, 58, 59, 61, 67, 68, 69, 75, 77, 78, 79):
        continue

    print()
    print(conv_id, "  ", topic['title'])

    for turn in topic['turn']:
        turn_id = turn['number']
        utterance = turn['raw_utterance']
        topic_turn_id = '%d_%d'% (conv_id, turn_id)
        
        print(topic_turn_id, utterance)
        topics[topic_turn_id] = utterance



========================================== Training conversations =====

1    Career choice for Nursing and Physician's Assistant
1_1 What is a physician's assistant?
1_2 What are the educational requirements required to become one?
1_3 What does it cost?
1_4 What's the average starting salary in the UK?
1_5 What about in the US?
1_6 What school subjects are needed to become a registered nurse?
1_7 What is the PA average salary vs an RN?
1_8 What the difference between a PA and a nurse practitioner?
1_9 Do NPs or PAs make more?
1_10 Is a PA above a NP?
1_11 What is the fastest way to become a NP?
1_12 How much longer does it take to become a doctor after being an NP?

2    Goat breeds
2_1 What are the main breeds of goat?
2_2 Tell me about boer goats.
2_3 What breed is good for meat?
2_4 Are angora goats good for it?
2_5 What about boer goats?
2_6 What are pygmies used for?
2_7 What is the best for fiber production?
2_8 How long do Angora goats live?
2_9 Can you milk them?
2_10 How ma

Search example:

In [4]:
elastic = es.ESSimpleAPI()
results = elastic.search_body(topics['33_1'], numDocs = 10)
print(results)

    _index _type  ...     _score                                       _source.body
0  msmarco  _doc  ...  13.568718  The film only adapts the first half of the boo...
1  msmarco  _doc  ...  12.347090  The NeverEnding Story (German: Die unendliche ...
2  msmarco  _doc  ...  12.184238  The NeverEnding Story was the first film adapt...
3  msmarco  _doc  ...  12.141284  The name of Atrayu's horse in the neverending ...
4  msmarco  _doc  ...  11.893921  Goodbye to the old Neverending Story and Hello...
5  msmarco  _doc  ...  11.884571  The NeverEnding Story III, starring Jason Jame...
6  msmarco  _doc  ...  11.654294  Noah Hathaway. Noah Leslie Hathaway (born Nove...
7  msmarco  _doc  ...  11.639892  The Neverending Story (German: Die unendliche ...
8  msmarco  _doc  ...  11.605606  Plot summary. The book centers on a boy, Basti...
9  msmarco  _doc  ...  11.429349  Synopsis: THE NEVER ENDING STORY centers on yo...

[10 rows x 5 columns]


## Retrieval with the training conversations
The ElasticSearchSimpleAPI notebook illustrates how to use ElasticSearch. Use this API to retrieve the top 100 ranked passages for each conversation turn. 

To evaluate the results you should use the provided `ConvSearchEvaluation` class. Examine and discuss the recall metric results. In terms of metrics, discuss what should be your goals for each step of the project.

In [5]:
import TRECCASTeval as trec
import numpy as np

import ElasticSearchSimpleAPI as es
import numpy as np

import pprint as pprint

elastic = es.ESSimpleAPI()
test_bed = trec.ConvSearchEvaluation()

_recall = 0
_p10 = 0
_ndcg5 = 0

_nturns = 0

for topic in test_bed.train_topics:
    
    conv_id = topic['number']
    if conv_id not in (1, 2, 4, 7, 15, 17,18,22,23,24,25,27,30):
        continue
        
    for turn in topic['turn']:
        turn_id = turn['number']
        utterance = turn['raw_utterance']
        topic_turn_id = '%d_%d'% (conv_id, turn_id)
        
        aux = test_bed.relevance_judgments.loc[test_bed.relevance_judgments['topic_turn_id'] == (topic_turn_id)]
        num_rel = aux.loc[aux['rel'] != 0]['docid'].count()
        
        if num_rel == 0:
            continue

        result = elastic.search_body(query=utterance, numDocs = 100)

        if np.size(result) == 0 or num_rel == 0:
            print(topic_turn_id, utterance, num_rel, "NO RESULTS")
            continue
        else:
            print(topic_turn_id, utterance, num_rel)

        [p10, recall, ap, ndcg5] = test_bed.eval(result[['_id','_score']], topic_turn_id)

#        print('P10=', p10, '  Recall=', recall, '  NDCG=',ndcg)
        _recall = _recall + recall
        _p10 = _p10 + p10
        _ndcg5 = _ndcg5 + ndcg5
        
        _nturns = _nturns + 1


_p10 = _p10/_nturns
_recall = _recall/_nturns
_ndcg5 = _ndcg5/_nturns

print()
print('P10=', _p10, '  Recall=', _recall, '  NDCG@5', _ndcg5)


1_1 What is a physician's assistant? 5
1_2 What are the educational requirements required to become one? 11
1_3 What does it cost? 4
1_4 What's the average starting salary in the UK? 1
1_5 What about in the US? 12 NO RESULTS
1_6 What school subjects are needed to become a registered nurse? 8
1_7 What is the PA average salary vs an RN? 3
1_8 What the difference between a PA and a nurse practitioner? 4
1_9 Do NPs or PAs make more? 15
1_10 Is a PA above a NP? 1
1_11 What is the fastest way to become a NP? 3
2_1 What are the main breeds of goat? 1
2_2 Tell me about boer goats. 14
2_3 What breed is good for meat? 7
2_4 Are angora goats good for it? 3
2_5 What about boer goats? 13
2_6 What are pygmies used for? 3
2_7 What is the best for fiber production? 3
2_9 Can you milk them? 2
2_10 How many can you have per acre? 3
2_11 Are they profitable? 3
4_1 What was the neolithic revolution? 15
4_2 When did it start and end? 9
4_3 Why did it start? 6
4_4 What did the neolithic invent? 3
4_5 What t

## Retrieval with the test conversations

In [6]:
import TRECCASTeval as trec
import numpy as np

from bert_serving.client import BertClient
from sklearn.metrics.pairwise import cosine_similarity

import ElasticSearchSimpleAPI as es
import numpy as np

import pprint as pprint

elastic = es.ESSimpleAPI()
test_bed = trec.ConvSearchEvaluation()

_recall = 0
_p10 = 0
_ndcg5 = 0
_nturns = 0
for topic in test_bed.test_topics:
    
    conv_id = topic['number']
    if conv_id not in (31, 32, 33, 34, 37, 40, 49, 50, 54, 56, 58, 59, 61, 67, 68, 69, 75, 77, 78, 79):
        continue

    for turn in topic['turn']:
        turn_id = turn['number']
        utterance = turn['raw_utterance']
        topic_turn_id = '%d_%d'% (conv_id, turn_id)
        
        aux = test_bed.test_relevance_judgments.loc[test_bed.test_relevance_judgments['topic_turn_id'] == (topic_turn_id)]
        num_rel = aux.loc[aux['rel'] != 0]['docid'].count()
        
        if num_rel == 0:
            continue

        result = elastic.search_body(query=utterance, numDocs = 100)

        if np.size(result) == 0 or num_rel == 0:
            print(topic_turn_id, utterance, num_rel, "NO RESULTS")
            continue
        else:
            print(topic_turn_id, utterance, num_rel)

        [p10, recall, ap, ndcg5] = test_bed.eval(result[['_id','_score']], topic_turn_id)

#        print('P10=', p10, '  Recall=', recall, '  NDCG=',ndcg)
        _recall = _recall + recall
        _p10 = _p10 + p10
        _ndcg5 = _ndcg5 + ndcg5
        
        _nturns = _nturns + 1

_p10 = _p10/_nturns
_recall = _recall/_nturns
_ndcg5 = _ndcg5/_nturns

print()
print('P10=', _p10, '  Recall=', _recall, '  NDCG@5', _ndcg5)


31_1 What is throat cancer? 89
31_2 Is it treatable? 77
31_3 Tell me about lung cancer. 171
31_4 What are its symptoms?  98
31_5 Can it spread to the throat? 58
31_6 What causes throat cancer? 63
31_7 What is the first sign of it? 58
31_8 Is it the same as esophageal cancer? 68
31_9 What's the difference in their symptoms? 55
32_1 What are the different types of sharks? 96
32_2 Are sharks endangered?  If so, which species? 67
32_3 Tell me more about tiger sharks. 98
32_4 What is the largest ever to have lived on Earth? 17
32_5 What's the biggest ever caught? 43
32_6 What about for great whites? 17
32_7 Tell me about makos. 88
32_8 What are their adaptations? 17
32_9 Where do they live? 20
32_10 What do they eat? 16
32_11 How do they compare with tigers for being dangerous? 9
33_1 Tell me about the Neverending Story film. 46
33_2 What is it about? 17 NO RESULTS
33_3 How was it received? 16
33_4 Did it win any awards? 4
33_5 Was it a book first? 35
33_6 Who was the author and when what i

## Passage re-Ranking
The Passage Ranking notebook example illustrates how to use the BERT service to compute the similarity between sentences. Using the BERT service, improve a passage ranking method to rerank the initial retrieval step.

To evaluate the results you should use the provided `ConvSearchEvaluation` class.


## Conversation Context Modeling

Conversation State Tracking example ilustrates how to use the 

To evaluate the results you should use the provided `ConvSearchEvaluation` class.
